In [1]:
import pandas as pd
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM, TrainingArguments, Trainer, BitsAndBytesConfig, EarlyStoppingCallback, PreTrainedTokenizer
from torch.utils.data import DataLoader
import sys
from peft import LoraConfig, get_peft_model, TaskType
from huggingface_hub import snapshot_download
import os
import re
import contextlib #helps make pip silent
import sys
import os
import numpy as np

with contextlib.redirect_stdout(sys.__stdout__), contextlib.redirect_stderr(sys.__stderr__):
    %pip install datasets
    %pip install sql_metadata
""""
with contextlib.redirect_stdout(sys.__stdout__), contextlib.redirect_stderr(sys.__stderr__):
    %pip install datasets
    %pip install sql_metadata
"""
from datasets import Dataset
from sql_metadata import Parser

In [2]:
is_google_colab = True
use_bnb = False

In [3]:
current_read_path = "./"
current_write_path = "./"

def read_path(rel_path):
    return os.path.join(current_read_path, rel_path)

def write_path(rel_path):
    return os.path.join(current_write_path, rel_path)

if is_google_colab:
    from google.colab import drive
    drive.mount('/content/drive')
    current_write_path = "/content/drive/MyDrive/sql_gen"

    hugging_face_path = snapshot_download(
        repo_id="USC-Applied-NLP-Group/SQL-Generation",
        repo_type="model",
        allow_patterns=["train-data/*", "deepseek-coder-1.3b-instruct/*", "src/*", "nba-data/*"],
    )
    sys.path.append(hugging_face_path)
    current_read_path = hugging_face_path
else:
    base_path = os.getcwd()  # Use current working directory in notebooks
    sys.path.append(os.path.abspath(os.path.join(base_path, '../..')))

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Fetching 37 files:   0%|          | 0/37 [00:00<?, ?it/s]

In [4]:
from src.prompts.pre_rag_prompt import input_text as input_prompt

In [5]:
MODEL_DIR = write_path("dyn_rag_test")
VAL_OUTPUT = write_path("dyn_rag_test.hf")

## Prepare Model

In [6]:

df = pd.read_csv(read_path("train-data/sql_train.tsv"), sep='\t')
df = df.applymap(lambda x: re.sub(r'\s+', ' ', x) if isinstance(x, str) else x)

# Display dataset info
print(f"Total dataset examples: {len(df)}")

# Load tokenizer
model_name = read_path("deepseek-coder-1.3b-instruct")
tokenizer = AutoTokenizer.from_pretrained(model_name)

# Enable 8-bit quantization for lower memory usage
bnb_config = None
if use_bnb:
    bnb_config = BitsAndBytesConfig(
        load_in_8bit=True,
        bnb_8bit_compute_dtype=torch.float16
    )

# Load model with quantization
#device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device_name = 'cuda' if torch.cuda.is_available() else 'cpu'
device = torch.device(device_name)
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    quantization_config=bnb_config,
    device_map=device
)

tokenizer.truncation_side = "left"


<ipython-input-6-ac29fbf828da>:2: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df = df.applymap(lambda x: re.sub(r'\s+', ' ', x) if isinstance(x, str) else x)


Total dataset examples: 1044


In [7]:
natural_query_list = df["natural_query"].tolist()
sql_query_list = df["sql_query"].tolist()
tables = [Parser(sql_query).tables for sql_query in sql_query_list]

dataset_dict = {
    "natural_query": natural_query_list,
    "tables": tables,
}

# Create HuggingFace Dataset
dataset = Dataset.from_dict(dataset_dict)

In [8]:

def format_deepseek_chat(example, tokenizer):
    # Manually build the prompt as one flat string
    prompt = f"{input_prompt}{example['natural_query']}\n"
    completion = f"Tables:\n{example['tables']}"

    full_text = prompt + completion
    tokenized = tokenizer(
        full_text,
        truncation=True,
        padding="max_length",
        max_length=3156,  # or whatever your model can handle
    )

    # Mask out prompt tokens in the labels
    prompt_len = len(tokenizer(prompt, truncation=True)["input_ids"])
    labels = tokenized["input_ids"][:]
    labels[:prompt_len] = [-100] * prompt_len
    tokenized["labels"] = labels

    return tokenized


In [9]:


# Apply formatting
tokenized_dataset = dataset.map(
    lambda x: format_deepseek_chat(x, tokenizer),
    remove_columns=["natural_query", "tables"]
)

# Split into train/validation
split = int(0.9 * len(tokenized_dataset))  # 90% train, 10% validation
train_dataset = tokenized_dataset.select(range(split))
val_dataset = tokenized_dataset.select(range(split, len(tokenized_dataset)))

print(len(train_dataset))
print(len(val_dataset))

for v in val_dataset:
    print(v)
    break

Map:   0%|          | 0/1044 [00:00<?, ? examples/s]

939
105
{'input_ids': [32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 3201

In [10]:
# Define LoRA configuration
lora_config = LoraConfig(
    r=16,  # Rank of LoRA matrices (adjust for memory vs. accuracy)
    lora_alpha=32,  # Scaling factor
    lora_dropout=0.0,  # Dropout for regularization
    bias="none",
    task_type=TaskType.CAUSAL_LM,
    target_modules=[
        "q_proj",
        "k_proj",
        "v_proj",
        "o_proj",
        "gate_proj",
        "up_proj",
        "down_proj"
    ]
)

# Wrap model with LoRA adapters
model = get_peft_model(model, lora_config)
model = model.to(device)
model.print_trainable_parameters()  # Show trainable parameters count

trainable params: 14,991,360 || all params: 1,361,463,296 || trainable%: 1.1011


In [11]:
training_args = TrainingArguments(
    output_dir=MODEL_DIR,
    eval_strategy="epoch",  # Evaluate at the end of each epoch
    save_strategy="epoch",  # Save model every epoch
    per_device_train_batch_size=1,  # LoRA allows higher batch size
    per_device_eval_batch_size=1,
    gradient_accumulation_steps=16,
    num_train_epochs=10,  # Increase if needed
    learning_rate=5e-5,  # Higher LR since we're only training LoRA layers
    weight_decay=0.001,
    logging_steps=50,  # Print loss every 50 steps
    save_total_limit=2,  # Keep last 4 checkpoints
    bf16=True if torch.cuda.is_available() else False,
    push_to_hub=False,
    load_best_model_at_end=True,
    metric_for_best_model="eval_loss",
    greater_is_better=False
)

# Trainer setup
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    tokenizer=tokenizer,
    callbacks=[EarlyStoppingCallback(early_stopping_patience=2)]
)

<ipython-input-11-319f42a4ed7b>:21: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(
No label_names provided for model class `PeftModelForCausalLM`. Since `PeftModel` hides base models input arguments, if label_names is not given, label_names can't be set automatically within `Trainer`. Note that empty label_names list will be used instead.


In [ ]:
# Run training
trainer.train()

# Merge LoRA adapters with the base model before saving
model = model.merge_and_unload()
model.save_pretrained(MODEL_DIR)
tokenizer.save_pretrained(MODEL_DIR)

wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.
wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.
wandb: Currently logged in as: licesma (licesma-usc) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


In [ ]:

# Prepare query with the same prompt
input_text = "How many points do the Los Angeles Lakers average at home?"
message = [{'role': 'user', 'content': input_prompt + input_text}]
inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)

# Generate Tables
outputs = model.generate(
    inputs,
    max_new_tokens=256,
)
model_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)

print("Generated Tables:", model_output)

In [ ]:
import sqlite3 as sql

prompt_length = len(input_prompt)

print(prompt_length)

# Create connection to sqlite3 database
connection = sql.connect(read_path('nba-data/nba.sqlite'))
cursor = connection.cursor()

for v in val_dataset:
    full_example = tokenizer.decode(v["input_ids"], skip_special_tokens=True)
    user_prompt = full_example[:prompt_length]
    question, tables = full_example[prompt_length:].split("Tables:\n")
    print(question)
    print(tables)
    break


In [ ]:
def extract_tables_from_string(s):
    keywords = {"game", "team", "other_stats"}
    found = {k for k in keywords if k in s}
    return found

In [ ]:
def compare_table_lists(actual_tables, generated_tables):
    actual_set = extract_tables_from_string(actual_tables)
    generated_set = extract_tables_from_string(generated_tables)

    # Check if they match
    return generated_set == actual_set

In [ ]:

num_sql_matched = 0

first_actual = []
first_model = []
print("Evaluating...")
for v in val_dataset:
    full_example = tokenizer.decode(v["input_ids"], skip_special_tokens=True)
    user_prompt = full_example[:prompt_length]
    question, training_tables = full_example[prompt_length:].split("Tables:\n")
    #print(question)
    #print(sql_query)

    # Obtain model output
    message = [{'role': 'user', 'content': input_prompt + question}]
    inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)

    # Generate SQL query
    outputs = model.generate(
        inputs,
        max_new_tokens=256,
        pad_token_id=tokenizer.eos_token_id,
    )
    model_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)
    after_last_colon = model_output.rsplit(":", 1)[-1]
    tables_string = after_last_colon.replace('\n', '').replace('\r', '')
    #print("Training tables:", training_tables)
    #print("Model tables:", tables_string.split(" "))
    first_actual = training_tables
    first_model = tables_string
    result = compare_table_lists(training_tables, tables_string)
    if result:
        num_sql_matched += 1

print("Accuracy :", num_sql_matched/len(val_dataset))



In [ ]:

num_sql_matched = 0

first_actual = []
first_model = []
print("Evaluating...")
for v in val_dataset:
    full_example = tokenizer.decode(v["input_ids"], skip_special_tokens=True)
    user_prompt = full_example[:prompt_length]
    question, training_tables = full_example[prompt_length:].split("Tables:\n")
    #print(question)
    #print(sql_query)

    # Obtain model output
    message = [{'role': 'user', 'content': input_prompt + question}]
    inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)

    # Generate SQL query
    outputs = model.generate(
        inputs,
        max_new_tokens=256,
        pad_token_id=tokenizer.eos_token_id,
    )
    model_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)
    after_last_colon = model_output.rsplit(":", 1)[-1]
    tables_string = after_last_colon.replace('\n', '').replace('\r', '')
    #print("Training tables:", training_tables)
    #print("Model tables:", tables_string.split(" "))
    first_actual = training_tables
    first_model = tables_string
    result = compare_table_lists(training_tables, tables_string)
    if result:
        num_sql_matched += 1

print("Accuracy :", num_sql_matched/len(val_dataset))



In [ ]:
model = AutoModelForCausalLM.from_pretrained(MODEL_DIR, torch_dtype=torch.bfloat16, device_map=device)
tokenizer = AutoTokenizer.from_pretrained(MODEL_DIR)
